# Crossover Swath

In [ ]:
import subprocess

import distributed

# Guessing installed cluster type
c = subprocess.run("qstat", capture_output=True, shell=True)

if c.returncode != 0:
    cluster_type = "slurm"
else:
    cluster_type = "sge"

In [ ]:
import numpy as np
import swot_calval.io
from casys.readers import ScCollectionReader
from octantng.core.dask import DaskCluster

from casys import CasysPlot, DataParams, PlotParams, SwathData

SwathData.enable_loginfo()

In [ ]:
dask_cluster = DaskCluster(cluster_type=cluster_type, jobs=(10, 10), memory=4)

dask_client = dask_cluster.client
dask_cluster.wait_for_workers(n_workers=3, timeout=600)

## Reader and container definition

Load the crossover table:

In [ ]:
crossover_table = swot_calval.io.load_crossover_table(
    "/data/OCTANT_NG/tests/ce_swot/swot_science_2015.parquet",
    latitude=80,
    percentage_of_land=15,
)

Initialize the collection reader:

In [ ]:
collection_path = "/data/OCTANT_NG/tests/ce_swot/zcollection/"

variables = [
    "cross_track_distance",
    "cycle_number",
    "latitude_nadir",
    "latitude",
    "longitude_nadir",
    "longitude",
    "pass_number",
    "time",
    "ssh_karin",
    "swh_karin",
]

reader = ScCollectionReader(
    data_path=collection_path,
    backend_kwargs={
        "cycle_numbers": 10,
        "pass_numbers": np.arange(100),
        "selected_variables":  variables,
    },
    time="time",
    latitude="latitude",
    longitude="longitude",
    latitude_nadir="latitude_nadir",
    longitude_nadir="longitude_nadir",
    cycle_number="cycle_number",
    pass_number="pass_number",
)

In [ ]:
sd = SwathData(source=reader)

## Definition of the crossover diagnostic

Using the [add_crossover_stat](../generated/casys.computation.rst#casys.computation.SwathData.add_crossover_stat) method:

In [ ]:
sd.add_crossover_stat(
    name="SSH Crossover",
    field=sd.fields["ssh_karin"],
    stats=["mean", "std"],
    temporal_stats_freq=["1h", "DAY"],
    max_time_difference="10 days",
    crossover_table=crossover_table,
    diamond_relocation=True,
    diamond_reduction="mean",
)

In [ ]:
sd.add_crossover_stat(
    name="SWH Crossover",
    field=sd.fields["swh_karin"],
    stats=["mean", "std"],
    temporal_stats_freq=["1h", "DAY"],
    max_time_difference="10 days",
    crossover_table=crossover_table,
    diamond_relocation=True,
    diamond_reduction="mean",
)

In [ ]:
sd.add_crossover_stat(
    name="SWH Crossover no relocation",
    field=sd.fields["swh_karin"],
    stats=["mean", "std"],
    temporal_stats_freq=["1h", "DAY"],
    max_time_difference="10 days",
    crossover_table=crossover_table,
    diamond_relocation=False,
    diamond_reduction="mean",
)

<div class="alert alert-block alert-info">

**Note**
The reduction step occurs after computing binning diagnostics.

</div>


## Computation

The two crossover diagnostic on `ssh_karin` and `swh_karin` values will be computed simultaneously (same computation parameters).

In [ ]:
sd.compute_dask()

<div class="alert alert-block alert-info">

**Note**
Crossover diagnostics can be computed without crossover table input, at computation time cost.

</div>


## Plot

### Along time diagnostic

Plot the temporal diagnostic, for a specific statistic and frequency:

- `mean` statistic and `1h` frequency for `ssh_karin`

In [ ]:
plot_along_time_ssh = CasysPlot(
    data=sd,
    data_name="SSH Crossover",
    stat="mean",
    freq="1h",
    data_params=DataParams(remove_nan=True),
)
plot_along_time_ssh.add_stat_bar()
plot_along_time_ssh.show()

- `std` statistic and `DAY` frequency for `swh_karin`

In [ ]:
plot_along_time_swh = CasysPlot(
    data=sd,
    data_name="SWH Crossover",
    stat="std",
    freq="DAY",
    data_params=DataParams(remove_nan=True),
)
plot_along_time_swh.add_stat_bar()
plot_along_time_swh.show()

### Geographical box diagnostics

Plot the geobox diagnostics, providing the diagnostic name and a specific statistic:

- `mean` statistic for `ssh_karin`

In [ ]:
plot_geobox_mean = CasysPlot(
    data=sd,
    data_name="SSH Crossover",
    stat="mean",
    plot_params=PlotParams(color_limits=(-3, 3)),
)
plot_geobox_mean.add_stat_bar()
plot_geobox_mean.show()

- `std` statistic for `swh_karin`

In [ ]:
plot_geobox_std = CasysPlot(
    data=sd,
    data_name="SWH Crossover",
    stat="std",
)
plot_geobox_std.add_stat_bar()
plot_geobox_std.show()

For the crossover diagnostic on swh without diamond relocation, we can notice small differences:

In [ ]:
plot_geobox_no_reloc = CasysPlot(
    data=sd,
    data_name="SWH Crossover no relocation",
    stat="std",
)
plot_geobox_no_reloc.add_stat_bar()
plot_geobox_no_reloc.show()

### Field and time differences at crossovers

Plot the time or field value at crossover points (on the full diamonds or at nadir coordinates depending on the `diamond_reduction` parameter).

#### Field delta values

For field values at crossover points. Here `diamond_reduction='mean'`, the field value is the averaged value of the field difference on the crossover diamond.

In [ ]:
plot_field_delta = CasysPlot(
    data=sd,
    data_name="SWH Crossover",
    delta="field",
)
plot_field_delta.add_stat_bar()
plot_field_delta.show()

#### Time delta values

For time difference at crossover points:

In [ ]:
plot_time_delta = CasysPlot(
    data=sd,
    data_name="SSH Crossover",
    delta="time",
)
plot_time_delta.add_stat_bar()
plot_time_delta.show()

## Example without crossovers diamond reduction

Query the collection a few passes and repeat the previous steps with `diamond_reduction=False` for the crossover diagnostic:

- Creating SwathData object:

In [ ]:
reader_part = ScCollectionReader(
    data_path=collection_path,
    backend_kwargs={
        "cycle_numbers": 10,
        "pass_numbers": [1, 154, 2, 155],
        "selected_variables": variables,
    },
    time="time",
    latitude="latitude",
    longitude="longitude",
    latitude_nadir="latitude_nadir",
    longitude_nadir="longitude_nadir",
    cycle_number="cycle_number",
    pass_number="pass_number",
)

In [ ]:
sd_part = SwathData(source=reader_part)

- Adding the crossover diagnostic with `diamond_reduction=False`:

In [ ]:
sd_part.add_crossover_stat(
    name="SSH Crossover",
    field=sd_part.fields["ssh_karin"],
    stats="mean",
    max_time_difference="10 days",
    crossover_table=crossover_table,
    diamond_relocation=True,
    diamond_reduction="none",
)

- Computing the diagnostic:

In [ ]:
sd_part.compute()

- Plot the field value difference for crossover diamond points:

In [ ]:
plot_field_delta = CasysPlot(
    data=sd_part,
    data_name="SSH Crossover",
    delta="field",
    plot_params=PlotParams(grid=True, y_limits=(-60, 60)),
)
plot_field_delta.add_stat_bar()
plot_field_delta.show()

- Zoom on a crossover diamond:

In [ ]:
plot_field_delta = CasysPlot(
    data=sd_part,
    data_name="SSH Crossover",
    delta="field",
    plot_params=PlotParams(grid=True, y_limits=(-3, 7), x_limits=(-150, -140)),
)
plot_field_delta.show()

- Plot the time difference value for crossover diamond points:

In [ ]:
plot_time_delta = CasysPlot(
    data=sd_part,
    data_name="SSH Crossover",
    delta="time",
    plot_params=PlotParams(grid=True, y_limits=(-60, 60)),
)
plot_time_delta.add_stat_bar()
plot_time_delta.show()

- Zoom on another crossover diamond:

In [ ]:
plot_time_delta = CasysPlot(
    data=sd_part,
    data_name="SSH Crossover",
    delta="time",
    plot_params=PlotParams(grid=True, y_limits=(-8, 4), x_limits=(35, 60)),
)
plot_time_delta.show()

## Extracting results from diagnostic

Extract the result from the SwathData object specifying the diagnostic name:

In [ ]:
ssh_diag = sd_part.get_diagnostic(name="SSH Crossover")

The parameters passed to the diagnostic can be accessed through attributes.  
The various results are available via the [results](../generated/casys.computation.diagnostics.rst#casys.computation.diagnostics.CrossoverSwathDiag.results) attribute. The different type of diagnostic are:

- [data](../generated/casys.computation.diagnostics.rst#casys.computation.diagnostics.CrossoverResult.data): xarray dataset containing crossover difference, geobox binning and temporal binning results
- [delta](../generated/casys.computation.diagnostics.rst#casys.computation.diagnostics.CrossoverResult.delta): difference results at crossover diamond points (reduced to crossover nadir points if the parameter `diamond_reduction` was filled)

In [ ]:
ssh_diag.results.delta

- geo_box: geographic binning results
- temporal: along time binning results
- locations: structured array containing crossovers details (lon, lat, cycle_numbers, pass_numbers)

In [ ]:
ssh_diag.results.locations

In [ ]:
dask_cluster.close()

To learn more about crossovers definition, please visit this documentation [page](../diagnostics/crossovers_stat_swath.rst).